In [3]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Example data for the first choropleth map
# data1 = dict(
#     # type = 'choropleth_mapbox',
#     locations = ['USA', 'CAN', 'MEX'],
#     z = [1, 2, 3],
#     locationmode = 'country names',
#     colorscale = 'Blues',
#     colorbar_title = 'Data 1'
# )

import numpy as np
import pandas as pd
from shapely.geometry import Polygon
import geopandas as gpd
import pyproj
pyproj.datadir.set_data_dir('/Users/jm/Code/mapgpt-mvp/.conda/share/proj')
import matplotlib.pyplot as plt
import os
import sys
from dotenv import load_dotenv
import pandas as pd
import pydeck as pdk
from IPython.display import display
sys.path.append('../src')

from infrastructure.gpt4 import GPT4
from infrastructure.postgres_db import PostgresDB
from application.maps.choropleth_map import ChoroplethMap
import plotly.graph_objects as go

load_dotenv()

db_name = os.environ.get("DB_NAME")
db_user = os.environ.get("DB_USER")
db_password = os.environ.get("DB_PASSWORD")


db = PostgresDB(db_name=db_name, db_user=db_user, db_password=db_password)
comunas = db.run_gpd_query("SELECT * FROM comuna")

# Function to extract coordinates
def get_polygon_coordinates(geom):
    if geom.type == 'Polygon':
        return [(x, y) for x, y in geom.exterior.coords]
    elif geom.type == 'MultiPolygon':
        return [[(x, y) for x, y in polygon.exterior.coords] for polygon in geom.geoms][0]
    else:
        return None

comunas = comunas.to_crs(epsg=4326)
np.random.seed(9)
comunas = comunas.assign(
    lat = comunas.geom.centroid.y,
    lon = comunas.geom.centroid.x,
    coordinates = comunas.geom.apply(lambda geom: [list(coord) for coord in geom.geoms[0].exterior.coords]),
    coordinates2 = comunas.geom.apply(get_polygon_coordinates),
    score=lambda _df: np.random.randint(0, 101, size=len(_df)),
    
    
)
c = comunas.set_index("codigo").head(3)
d = comunas.set_index("codigo").tail(3)

data1 = dict(geojson=c.to_geo_dict(), 
                           locations=c.index, z=c.score, colorscale="viridis",
                           zmin=c.score.min(), zmax=c.score.max())
data2 = dict(geojson=d.to_geo_dict(), 
                           locations=d.index, z=d.score, colorscale="viridis",
                           zmin=d.score.min(), zmax=d.score.max())

# Example data for the second choropleth map
# data2 = dict(
#     # type = 'choropleth_mapbox',
#     locations = ['FRA', 'DEU', 'ITA'],
#     z = [4, 5, 6],
#     locationmode = 'country names',
#     colorscale = 'Reds',
#     colorbar_title = 'Data 2'
# )

# Create subplots with 1 row and 2 columns
fig = make_subplots(rows=1, cols=2, specs=[[{'type': 'mapbox'},{'type': 'mapbox'}]],
                    subplot_titles=("Choropleth 1", "Choropleth 2"))

# Add the first choropleth map to the first subplot
fig.add_trace(go.Choroplethmapbox(data1), row=1, col=1)

# Add the second choropleth map to the second subplot
fig.add_trace(go.Choroplethmapbox(data2), row=1, col=2)

# Update the layout of the figure
fig.update_layout(
    title_text='Multiple Choropleth Maps',
    height=600
)

# Show the figure
fig.show()

/var/folders/8j/bf4mjlj94czf88p79v8gb24w0000gp/T/ipykernel_29935/2950563583.py:56: UserWarning:

Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.


/var/folders/8j/bf4mjlj94czf88p79v8gb24w0000gp/T/ipykernel_29935/2950563583.py:57: UserWarning:

Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.


/var/folders/8j/bf4mjlj94czf88p79v8gb24w0000gp/T/ipykernel_29935/2950563583.py:46: ShapelyDeprecationWarning:

The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.

/var/folders/8j/bf4mjlj94czf88p79v8gb24w0000gp/T/ipykernel_29935/2950563583.py:48: ShapelyDeprecationWarning:

The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.



In [14]:
type(d.iloc[0]["geom"])

shapely.geometry.multipolygon.MultiPolygon

In [5]:
fig is None

False